In [1]:
import pyLPM
import pandas as pd
import RBFN
import numpy as np
from sklearn.preprocessing import MinMaxScaler

In [2]:
walter = pd.read_csv('data/walker.csv')

In [3]:
walter.drop(columns=['Id','U','T'], inplace=True)

In [4]:
walter.head()

X     Y      V
0  11.0   8.0    0.0
1   8.0  30.0    0.0
2   9.0  48.0  224.4
3   8.0  69.0  434.4
4   9.0  90.0  412.1

In [5]:
walter['Z'] = np.zeros(len(walter))

In [6]:
#walter.V=(walter.V-walter.V.min())/(walter.V.max()-walter.V.min())

In [7]:
walter.head()

X     Y      V    Z
0  11.0   8.0    0.0  0.0
1   8.0  30.0    0.0  0.0
2   9.0  48.0  224.4  0.0
3   8.0  69.0  434.4  0.0
4   9.0  90.0  412.1  0.0

In [8]:
coordinates = walter[['X','Y','Z']]

In [9]:
RBFN.cluster_centers_evaluation(coordinates=coordinates, 
                                max_num_clusters=40)

In [10]:
n_clus = 200

In [11]:
centers = RBFN.cluster_centers(n_clus=n_clus,
                               coordinates=coordinates)

In [12]:
rbf_n = RBFN.RBFN(cluster_centers=centers, 
          sigma=None)

In [13]:
rbf_n.knn_sigma_definition(neighbors_number=5)

In [14]:
rbf_n.random_bias()

Random bias: 0.5606922369675975


In [15]:
rbf_n.fit(X=coordinates.values, 
          y=walter.V.values)

In [16]:
grid = pyLPM.utils.autogrid(x=walter.X, y=walter.Y, z=walter.Z, sx=5, sy=5, sz=1)

In [17]:
X = pyLPM.utils.add_coord(grid)

In [18]:
predict = rbf_n.predict(X)

In [19]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [20]:
X_train, X_test, y_train, y_test = RBFN.train_test_sets_builder(walter, 'X', 'Y', 'Z', 'V')

In [21]:
rbf_n.train(4000, X_train, X_test, y_train, y_test, learning_rate_w=0.00001)

In [22]:
predict_train = rbf_n.predict(X)

In [23]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_train,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [24]:
rbf_n.weights = np.random.randn(n_clus+1)

In [25]:
predict_random_weights = rbf_n.predict(X)

In [26]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_random_weights,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [27]:
rbf_n.train(10000, X_train, X_test, y_train, y_test, learning_rate_w=0.0006)

In [28]:
predict_trained_weights = rbf_n.predict(X)

In [29]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_weights,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [30]:
rbf_n.weights = np.random.randn(n_clus+1)

In [31]:
rbf_n.train(3000, X_train, X_test, y_train, y_test, neighbors_number=3, learning_rate_w=0.0006)

Epoch: 0 
 Mean loss: 135079.1061762749
Epoch: 500 
 Mean loss: 17157.696737558188
Epoch: 1000 
 Mean loss: 10670.890561101929
Epoch: 1500 
 Mean loss: 8420.889755721497
Epoch: 2000 
 Mean loss: 7292.302137985551
Epoch: 2500 
 Mean loss: 6571.559335970584


In [32]:
predict_trained_knn = rbf_n.predict(X)

In [33]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [34]:
pyLPM.plots.scatter2d(x=predict_trained_weights, y=predict_trained_knn)

In [35]:
rbf_n.weights = np.random.randn(n_clus+1)

In [36]:
rbf_n.train(3000, X_train, X_test, y_train, y_test, neighbors_number=6, learning_rate_w=0.0006)

Epoch: 0 
 Mean loss: 134597.52253681867
Epoch: 500 
 Mean loss: 17166.004745469923
Epoch: 1000 
 Mean loss: 10672.592110267682
Epoch: 1500 
 Mean loss: 8420.46849698725
Epoch: 2000 
 Mean loss: 7291.122918820809
Epoch: 2500 
 Mean loss: 6570.166474697944


In [37]:
predict_trained_knn_6 = rbf_n.predict(X)

In [38]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn_6,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [39]:
pyLPM.plots.scatter2d(x=predict_trained_knn_6, y=predict_trained_knn)

In [40]:
rbf_n.weights = np.random.randn(n_clus+1)

In [41]:
rbf_n.fit(X=coordinates.values, 
          y=walter.V.values)

In [42]:
rbf_n.train(6000, X_train, X_test, y_train, y_test, neighbors_number=5, learning_rate_w=0.003)

Epoch: 0 
 Mean loss: 7917.426346809904
Epoch: 500 
 Mean loss: 4253.253473275633
Epoch: 1000 
 Mean loss: 3790.068347605296
Epoch: 1500 
 Mean loss: 3574.888367932821
Epoch: 2000 
 Mean loss: 3435.7952686489475
Epoch: 2500 
 Mean loss: 3330.7328810124927
Epoch: 3000 
 Mean loss: 3244.83461066711
Epoch: 3500 
 Mean loss: 3171.47485107813
Epoch: 4000 
 Mean loss: 3107.1508523057337
Epoch: 4500 
 Mean loss: 3049.7611594373348
Epoch: 5000 
 Mean loss: 2997.9241546298585
Epoch: 5500 
 Mean loss: 2950.6693170648814


In [43]:
predict_trained_knn_from_fit = rbf_n.predict(X)

In [44]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn_from_fit,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)